# Train/Validation/Test Split Notebook - Validation/Test Data Split  

Objective: Split the full dataset into Validation/Test data.  


##### Train data (other notebook):  
3 month data = January and February of 2015    
full data = 2015 through 2017    
Steps:   
A) Drop rows:  
- Where weather readings are suspect or erroneous   
- Where report_types are SY-MT, FM-16, SOD,SOM  
- Where there are nulls  
- Where there are 99999 (missing) data    

B) Bin Data    
C) Use train data to create Airport PageRank helper Table     
D) Join Airport PageRank to final table    
E) Create helper table of averages  grouped by day_of_week and origin for imputing validation data     
F) Create helper table of averages  for imputing validation data (when ORIGIN not in training data)     


 ##### Validation/Test Data (this notebook): 
3 month data = March 2015 (validation)  
full data = 2018 (validation), 2019 (test)    
Steps:  
A) Join PageRank helper table created previously to test data  
B) Imputations  
- Join imputed value table (averages at each ORIGIN) with full data (joins columns with feature averages to full data)  
- For averages with null values, impute with second helper table of averages of all training data (null averages are caused by ORIGIN in validation/test data that are not in train data)   
- Finally, impute the suspect or erroneous, nulls, and 99999 (missing) data in the full table with these averages  

C) Bin Data

In [0]:
#Import packages
from pyspark.sql import functions as f
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType, NullType, ShortType, DateType, BooleanType, BinaryType, FloatType
from pyspark.sql import SQLContext
from pyspark.sql.functions import isnan, when, count, col, udf, date_trunc, max as max_, sum as sum_, avg as avg_, min as min_
from pyspark.ml.feature import Bucketizer
from pyspark.sql.types import TimestampType
from pyspark.sql.functions import udf, date_trunc, col
from datetime import datetime, timedelta
from pyspark.sql.types import TimestampType
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from pytz import timezone
import pytz

sqlContext = SQLContext(sc)

## Get Joined Data from Shared Folder

In [0]:
## dbutils.fs.mkdirs("dbfs:/mnt/mids-w261/team_25/train_test_data_folder")               #Made Directory in DataBricks, no need to remake
# display(dbutils.fs.ls("dbfs:/mnt/mids-w261/team_25/train_test_data_folder"))

In [0]:
# Read Files and Fix Schema For Processing

#READING PARQUET File from Shared Directory
filename = "flight_weather_data_3m"              # 3 Month Data
joined_data_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/join_data_folder/"+filename+"/part-00*.parquet")

filename = "flight_weather_data"               # Full data
joined_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/join_data_folder/"+filename+"/part-00*.parquet")

joined_data_3m.display()
print("joined_data_3m Shape:", joined_data_3m.count(), len(joined_data_3m.columns))
joined_data.display()
print("joined_data Shape:", joined_data.count(), len(joined_data.columns))

#Fix Schema
joined_data_3m = joined_data_3m.withColumn('DAY_OF_WEEK',joined_data_3m.DAY_OF_WEEK.cast(IntegerType()) )
joined_data_3m = joined_data_3m.withColumn('FIRST_DEP',joined_data_3m.FIRST_DEP.cast(IntegerType()) )
joined_data_3m = joined_data_3m.withColumn('PREVIOUS_DELAY',joined_data_3m.PREVIOUS_DELAY.cast(IntegerType()) )
joined_data_3m = joined_data_3m.withColumn('CRS_DEP_TIME',joined_data_3m.CRS_DEP_TIME.cast(IntegerType()) )

joined_data = joined_data.withColumn('DAY_OF_WEEK',joined_data.DAY_OF_WEEK.cast(IntegerType()) )
joined_data = joined_data.withColumn('FIRST_DEP',joined_data.FIRST_DEP.cast(IntegerType()) )
joined_data = joined_data.withColumn('PREVIOUS_DELAY',joined_data.PREVIOUS_DELAY.cast(IntegerType()) )
joined_data = joined_data.withColumn('CRS_DEP_TIME',joined_data.CRS_DEP_TIME.cast(IntegerType()) )

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY DELAY LATITUDE LONGITUDE ELEVATION REPORT_TYPE WND_SPEED WND_SPEED_QUAL CIG_HEIGHT CIG_QUAL VIS_DIST VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP TEMP_QUAL DEW_TEMP DEW_TEMP_QUAL SLPRESS SLPRESS_QUAL DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_REPORT_TYPE DEST_WND_SPEED DEST_WND_SPEED_QUAL DEST_CIG_HEIGHT DEST_CIG_QUAL DEST_VIS_DIST DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP DEST_TEMP_QUAL DEST_DEW_TEMP DEST_DEW_TEMP_QUAL DEST_SLPRESS DEST_SLPRESS_QUAL FLIGHTS_PER_DAY 2015 1 4 AA DFW TX CLE OH 1415 155.0 1021.0 0 0 0 32.8978 -97.0189 170.7 FM-16 31 5 122 5 3219 5 N 5 6 5 0 5 99999 9 41.4057 -81.852 238.0 FM-15 88 5 22000 5 16093 5 N 5 -11 5 -128 5 10169 5 13951 2015 1 4 AA DFW TX DTW MI 1030 150.0 986.0 0 0 1 32.8978 -97.0189 170.7 FM-16 21 5 396 5 3219 5 N 5 -6 5 -17 5 99999 9 42.2313 -83.3308 192.3 FM-15 88 5 7315 5 16093 5 N 5 -72 5 -133 5 10171 5 13951 2015 1 4 AA DFW TX IND IN 1625 120.0 761.0 0 0 1 32.8978 -97.0189 170.7 FM-16 26 5 183 5 2414 5 N 5 17 5 6 5 99999 9 39.72517 -86.28168 241.1 FM-15 88 5 7620 5 16093 5 N 5 11 5 -94 5 10190 5 13951 2015 1 4 AA PHX AZ DFW TX 200 120.0 868.0 0 0 1 33.4277 -112.0038 337.4 SOM 9999 9 99999 9 999999 9 9 9 9999 9 9999 9 99999 9 32.8978 -97.0189 170.7 FM-15 26 5 1372 5 16093 5 N 5 11 5 -50 5 10296 5 13951 2015 1 4 AA PHX AZ DFW TX 200 120.0 868.0 0 0 1 33.4277 -112.0038 337.4 SOD 9999 9 99999 9 999999 9 9 9 9999 9 9999 9 99999 9 32.8978 -97.0189 170.7 FM-15 26 5 1372 5 16093 5 N 5 11 5 -50 5 10296 5 13951 2015 1 4 AS ATL GA SEA WA 1810 334.0 2182.0 0 0 1 33.6301 -84.4418 307.8 FM-15 15 5 1981 5 16093 5 N 5 133 5 -28 5 10250 5 47.4444 -122.3138 112.8 FM-15 21 5 22000 5 16093 5 N 5 44 5 -44 5 10263 5 13951 2015 1 4 AS OGG HI BLI WA 1425 353.0 2681.0 0 0 1 20.89972 -156.42861 15.5 FM-15 41 5 22000 5 16093 5 N 5 239 5 139 5 10122 5 48.79389 -122.53722 45.4 FM-15 15 5 22000 5 16093 5 N 5 39 5 -33 5 10263 5 13951 2015 1 4 AS SAT TX SEA WA 1830 270.0 1774.0 0 0 0 29.5443 -98.4839 240.5 FM-15 21 5 213 5 16093 5 N 5 50 5 33 5 10191 5 47.4444 -122.3138 112.8 FM-15 21 5 22000 5 16093 5 N 5 50 5 -50 5 10257 5 13951 2015 1 4 AS SEA WA GEG WA 1220 62.0 224.0 0 0 0 47.4444 -122.3138 112.8 FM-15 0 5 22000 5 16093 5 N 5 0 5 -44 5 10280 5 47.6216 -117.528 717.2 FM-15 0 5 853 5 12875 5 N 5 -106 5 -122 5 10335 5 13951 2015 1 4 B6 FLL FL BOS MA 1342 188.0 1237.0 0 1 1 26.07875 -80.16217 3.4 FM-15 0 5 1829 5 16093 5 N 5 250 5 206 5 10225 5 42.3606 -71.0097 3.7 FM-15 82 5 22000 5 16093 5 N 5 -11 5 -150 5 10175 5 13951 2015 1 4 B6 LAS NV LGB CA 705 65.0 231.0 0 0 0 36.0719 -115.1634 664.5 FM-15 31 5 5486 5 16093 5 N 5 6 5 -94 5 10169 5 33.8116 -118.1463 9.4 FM-15 0 5 22000 5 8047 5 N 5 28 5 -22 5 10192 5 13951 2015 1 4 DL ATL GA HOU TX 1615 142.0 696.0 0 0 0 33.6301 -84.4418 307.8 FM-15 21 5 1981 5 16093 5 N 5 133 5 -39 5 10254 5 29.63806 -95.28194 13.4 FM-15 46 5 305 5 9656 5 N 5 67 5 56 5 10219 5 13951 2015 1 4 DL BNA TN ATL GA 1200 75.0 214.0 0 0 0 36.11889 -86.68917 182.9 FM-15 21 5 1433 5 16093 5 N 5 6 5 -39 5 10294 5 33.6301 -84.4418 307.8 FM-15 21 5 7010 5 16093 5 N 5 83 5 -28 5 10285 5 13951 2015 1 4 DL LAX CA MCO FL 2225 277.0 2218.0 0 0 0 33.938 -118.3888 29.6 FM-15 0 5 22000 5 16093 5 N 5 100 5 44 5 10207 5 28.4339 -81.325 27.4 FM-15 41 5 61 5 0 A N A 172 5 172 5 10233 5 13951 2015 1 4 DL LAX CA MSY LA 1815 213.0 1670.0 0 0 0 33.938 -118.3888 29.6 FM-15 36 5 22000 5 16093 5 N 5 128 5 28 5 10199 5 29.99691 -90.27751 1.2 FM-16 36 5 884 5 14484 5 N 5 144 5 117 5 99999 9 13951 2015 1 4 DL MCI MO MSP MN 900 86.0 393.0 0 0 0 39.2972 -94.7306 306.3 FM-15 51 5 22000 5 16093 5 N 5 -94 5 -122 5 10249 5 44.8831 -93.2289 265.8 FM-15 51 5 2286 5 16093 5 N 5 -83 5 -122 5 10121 5 13951 2015 1 4 DL PBI FL LGA NY 800 163.0 1035.0 0 0 0 26.6847 -80.0994 5.8 FM-15 0 5 610 5 11265 5 N 5 222 5 211 5 10208 5 40.7792 -73.88 3.4 FM-15 51 5 22000 5 16093 5 

joined_data_3m Shape: 1400798 51

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY DELAY LATITUDE LONGITUDE ELEVATION REPORT_TYPE WND_SPEED WND_SPEED_QUAL CIG_HEIGHT CIG_QUAL VIS_DIST VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP TEMP_QUAL DEW_TEMP DEW_TEMP_QUAL SLPRESS SLPRESS_QUAL DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_REPORT_TYPE DEST_WND_SPEED DEST_WND_SPEED_QUAL DEST_CIG_HEIGHT DEST_CIG_QUAL DEST_VIS_DIST DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP DEST_TEMP_QUAL DEST_DEW_TEMP DEST_DEW_TEMP_QUAL DEST_SLPRESS DEST_SLPRESS_QUAL FLIGHTS_PER_DAY 2015 5 5 AA DFW TX AUS TX 2020 67.0 190.0 0 0 0 32.8978 -97.0189 170.7 FM-15 26 5 22000 5 16093 5 N 5 244 5 122 5 10152 5 30.1831 -97.6799 146.3 FM-15 31 5 22000 5 16093 5 N 5 267 5 111 5 10153 5 16927 2015 5 5 AA DFW TX ORD IL 700 146.0 802.0 0 0 0 32.8978 -97.0189 170.7 FM-15 36 5 22000 5 16093 5 N 5 161 5 106 5 10152 5 41.995 -87.9336 201.8 FM-15 26 5 22000 5 16093 5 N 5 33 5 11 5 10203 5 16927 2015 5 5 AA DFW TX SFO CA 905 233.0 1464.0 0 0 0 32.8978 -97.0189 170.7 FM-15 0 5 22000 5 16093 5 N 5 133 5 100 5 10165 5 37.6197 -122.3647 2.4 FM-15 26 5 22000 5 16093 5 N 5 144 5 89 5 10092 5 16927 2015 5 5 AA JFK NY BOS MA 1629 80.0 187.0 0 0 0 40.6386 -73.7622 3.4 FM-15 57 5 1097 5 16093 5 N 5 117 5 44 5 10154 5 42.3606 -71.0097 3.7 FM-15 57 5 7620 5 16093 5 N 5 89 5 39 5 10162 5 16927 2015 5 5 AA LAX CA LAS NV 1640 70.0 236.0 0 0 0 33.938 -118.3888 29.6 FM-15 57 5 5486 5 14484 5 N 5 194 5 128 5 10125 5 36.0719 -115.1634 664.5 FM-15 77 5 7620 5 16093 5 N 5 344 5 -61 5 10071 5 16927 2015 5 5 AA LGA NY MIA FL 1950 189.0 1096.0 0 0 0 40.7792 -73.88 3.4 FM-15 51 5 7620 5 16093 5 N 5 133 5 44 5 10136 5 25.7881 -80.3169 8.8 FM-15 41 5 22000 5 16093 5 N 5 289 5 94 5 10111 5 16927 2015 5 5 AA MCO FL ORD IL 1928 175.0 1005.0 0 0 0 28.4339 -81.325 27.4 FM-15 62 5 22000 5 16093 5 N 5 283 5 106 5 10109 5 41.995 -87.9336 201.8 FM-15 41 5 7620 5 16093 5 N 5 178 5 44 5 10193 5 16927 2015 5 5 AA ORD IL DFW TX 1325 154.0 802.0 0 1 1 41.995 -87.9336 201.8 FM-15 21 5 22000 5 16093 5 N 5 150 5 39 5 10221 5 32.8978 -97.0189 170.7 FM-15 46 5 22000 5 16093 5 N 5 228 5 139 5 10184 5 16927 2015 5 5 AA ORD IL DFW TX 900 163.0 802.0 0 0 0 41.995 -87.9336 201.8 FM-15 31 5 22000 5 16093 5 N 5 67 5 28 5 10214 5 32.8978 -97.0189 170.7 FM-15 0 5 22000 5 16093 5 N 5 133 5 100 5 10165 5 16927 2015 5 5 AS JNU AK ANC AK 1945 96.0 571.0 0 0 0 58.3566 -134.564 4.9 FM-15 57 5 1676 5 16093 5 N 5 94 5 50 5 10155 5 61.169 -150.0278 36.6 FM-15 31 5 7620 5 16093 5 N 5 122 5 6 5 10137 5 16927 2015 5 5 AS ORD IL SEA WA 800 267.0 1721.0 0 0 0 41.995 -87.9336 201.8 FM-15 26 5 22000 5 16093 5 N 5 33 5 17 5 10208 5 47.4444 -122.3138 112.8 FM-15 31 5 6096 5 16093 5 N 5 94 5 61 5 10193 5 16927 2015 5 5 AS SAN CA BOS MA 845 343.0 2588.0 0 0 0 32.7336 -117.1831 4.6 FM-15 0 5 7620 5 14484 5 N 5 172 5 144 5 10111 5 42.3606 -71.0097 3.7 FM-15 15 5 701 5 16093 5 N 5 78 5 44 5 10163 5 16927 2015 5 5 AS SEA WA SNA CA 1400 157.0 978.0 0 0 1 47.4444 -122.3138 112.8 FM-15 36 5 22000 5 16093 5 N 5 156 5 83 5 10189 5 33.68 -117.86639 16.5 FM-15 26 5 7620 5 16093 5 N 5 256 5 111 5 10122 5 16927 2015 5 5 B6 BOS MA EWR NJ 630 83.0 200.0 0 0 0 42.3606 -71.0097 3.7 FM-16 41 5 579 5 16093 5 N 5 70 5 30 5 99999 9 40.6825 -74.1694 2.1 FM-15 36 5 1829 5 16093 5 N 5 100 5 39 5 10132 5 16927 2015 5 5 B6 BOS MA SJU PR 2359 231.0 1674.0 0 0 0 42.3606 -71.0097 3.7 FM-15 31 5 22000 5 16093 5 N 5 56 5 33 5 10164 5 18.4325 -66.01083 2.7 FM-15 21 5 22000 5 16093 5 N 5 278 5 217 5 10150 5 16927 2015 5 5 B6 JFK NY ORD IL 1930 185.0 740.0 0 0 0 40.6386 -73.7622 3.4 FM-15 62 5 7620 5 16093 5 N 5 111 5 44 5 10146 5 41.995 -87.9336 201.8 FM-15 41 5 7620 5 16093 5 N 5 178 5 44 5 10193 5 16927 2015 5 5 DL ATL GA LAS NV 2146 269.0 1747.0 0 0 0 33.6301 -84.4418 307.8 FM-15 57 5 22000 5 16093 5 N 5 206 5 50 5 10150 5 36.0719 -115.1634 664.5 FM-15 93 5 7620 5 16093 5 N 5 344 5 -56 5 10055 5 16927

joined_data Shape: 31534960 51

## Split Data: 

###### Train data:  
3 month data = 1st and 2nd month  
full data = 2015 through 2017  

###### Validation/Test Data: 
3 month data = 3rd month (validation)
full data = 2018 (validation), 2019 (test)

In [0]:
train_3m        = joined_data_3m.where("MONTH < 3")
valid_test_3m   = joined_data_3m.where("MONTH > 2")
            
train           = joined_data.where("YEAR < 2018")
valid_test      = joined_data.where("YEAR > 2017")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test", True)      #remove file if there already is an existing one, be careful with this!!!

train_3m.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m")  
valid_test_3m.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m")                                    
train.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train")                                    
valid_test.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test")

In [0]:
#Read Data
train_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m/part-00*.parquet")
valid_test_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m/part-00*.parquet")
print("3-Month Train/Validation/Test:", train_3m.count(), valid_test_3m.count())

train = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train/part-00*.parquet")
valid_test = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test/part-00*.parquet")
print("Full Data Train/Validation/Test:", train.count(), valid_test.count())

3-Month Train/Validation/Test: 897251 503547
Full Data Train/Validation/Test: 17056263 14478697

# A) Add Page Rank
Join PageRank helper table to test data. Helper table created in train split notebook: https://dbc-c4580dc0-018b.cloud.databricks.com/?o=8229810859276230#notebook/2158640876511176/command/3450569410566968

In [0]:
#Read helper table Data
filename = "airportPR_ordered_df"                      
airportPR_ordered_df = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# airportPR_ordered_df.display()
airportPR_ordered_df.registerTempTable("airportPR_ordered_df_tt")
unique_pr_airports = airportPR_ordered_df.count()   #This is total of unique airports in pagerank calculated from training data

#Read Data
valid_test_3m.registerTempTable("valid_test_3m_tt") 
valid_test.registerTempTable("valid_test_tt") 

In [0]:
#Join Data

# 3 MONTH DATA
valid_test_3m_pr = spark.sql("""SELECT * 
                                FROM valid_test_3m_tt t1
                                LEFT JOIN airportPR_ordered_df_tt t2
                                ON (t1.ORIGIN = t2.original)
                                """).drop("original")

#SAVING Spark Dataframe to Shared Directory
file_to_store = valid_test_3m_pr                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "valid_test_3m_pr"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

############################################

# FULL DATA
valid_test_pr = spark.sql("""SELECT * 
                                FROM valid_test_tt t1
                                LEFT JOIN airportPR_ordered_df_tt t2
                                ON (t1.ORIGIN = t2.original)
                                """)

#SAVING Spark Dataframe to Shared Directory
file_to_store = valid_test_pr                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "valid_test_pr"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "valid_test_3m_pr"                      
valid_test_3m_pr = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# valid_test_3m_pr.display()
# print("valid_test_3m_pr Shape:", valid_test_3m_pr.count(), len(valid_test_3m_pr.columns))

############################################

filename = "valid_test_pr"                      
valid_test_pr = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# valid_test_pr.display()
# print("valid_test_pr:", valid_test_pr.count(), len(valid_test_pr.columns))

# B) Imputations

#### Join imputed value table (averages at each ORIGIN) with full data (joins columns with feature averages to full data)

In [0]:
#Read Imputed Value helper Table from training notebook: 

# 3 MONTH DATA
train_3m_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m_groupby/part-00*.parquet")
# train_3m_groupby.display()

#FULL DATA
train_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_groupby/part-00*.parquet")
# train_groupby.display()

In [0]:
#Inner Join train_data averages 

# 3 MONTH DATA
valid_test_3m_pr.registerTempTable("valid_test_3m_pr_tt")
train_3m_groupby.registerTempTable("train_3m_groupby_tt")

valid_test_3m_train_3m_groupby = spark.sql("""SELECT t1.*, t2.* 
             FROM(
                  (SELECT * FROM valid_test_3m_pr_tt) t1
                  LEFT JOIN
                  (SELECT * FROM train_3m_groupby_tt) t2
                  ON t1.DAY_OF_WEEK = t2.DOW AND t1.ORIGIN = t2.O
                  )
             """).drop("DOW","O")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_3m_train_3m_groupby.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby")  

#################################

# FULL DATA
valid_test_pr.registerTempTable("valid_test_pr_tt")
train_groupby.registerTempTable("train_groupby_tt")

valid_test_train_groupby = spark.sql("""SELECT t1.*, t2.* 
             FROM(
                  (SELECT * FROM valid_test_pr_tt) t1
                  LEFT JOIN
                  (SELECT * FROM train_groupby_tt) t2
                  ON t1.DAY_OF_WEEK = t2.MO AND t1.ORIGIN = t2.O
                  )
             """).drop("MO","O")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_train_groupby.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby")  

#### For averages with null values, impute with second helper table of averages of all training data (null averages are caused by ORIGIN in validation/test data that are not in train data)

In [0]:
#Read Data

# 3 MONTH DATA
valid_test_3m_train_3m_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby/part-00*.parquet")
# valid_test_3m_train_3m_groupby.display()

# FULL DATA
valid_test_train_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby/part-00*.parquet")
# valid_test_3m_train_3m_groupby.display()

In [0]:
# Read in Avg Lookup Table
avg_lookup = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/avg_lookup/part-00*.parquet")
avg_lookup.display()

#Impute null average readings

#3 MONTH DATA
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby.na.fill(value=avg_lookup.select("avg_DAY_OF_WEEKa").first()[0],subset=['avg_DAY_OF_WEEK'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_CRS_DEP_TIMEa").first()[0],subset=['avg_CRS_DEP_TIME'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_CRS_ELAPSED_TIMEa").first()[0],subset=['avg_CRS_ELAPSED_TIME'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DISTANCEa").first()[0],subset=['avg_DISTANCE'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("min_FIRST_DEPa").first()[0],subset=['min_FIRST_DEP'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("min_PREVIOUS_DELAYa").first()[0],subset=['min_PREVIOUS_DELAY'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_LATITUDEa").first()[0],subset=['avg_LATITUDE'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_LONGITUDEa").first()[0],subset=['avg_LONGITUDE'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_ELEVATIONa").first()[0],subset=['avg_ELEVATION'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_WND_SPEEDa").first()[0],subset=['avg_WND_SPEED'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_CIG_HEIGHTa").first()[0],subset=['avg_CIG_HEIGHT'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_VIS_DISTa").first()[0],subset=['avg_VIS_DIST'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_TEMPa").first()[0],subset=['avg_TEMP'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEW_TEMPa").first()[0],subset=['avg_DEW_TEMP'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_SLPRESSa").first()[0],subset=['avg_SLPRESS'])

valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_LATITUDEa").first()[0],subset=['avg_DEST_LATITUDE'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_LONGITUDEa").first()[0],subset=['avg_DEST_LONGITUDE'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_ELEVATIONa").first()[0],subset=['avg_DEST_ELEVATION'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_WND_SPEEDa").first()[0],subset=['avg_DEST_WND_SPEED'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_CIG_HEIGHTa").first()[0],subset=['avg_DEST_CIG_HEIGHT'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_VIS_DISTa").first()[0],subset=['avg_DEST_VIS_DIST'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_TEMPa").first()[0],subset=['avg_DEST_TEMP'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_DEW_TEMPa").first()[0],subset=['avg_DEST_DEW_TEMP'])
valid_test_3m_train_3m_groupby1=valid_test_3m_train_3m_groupby1.na.fill(value=avg_lookup.select("avg_DEST_SLPRESSa").first()[0],subset=['avg_DEST_SLPRESS'])
#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby1", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_3m_train_3m_groupby1.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby1") 


#FULL DATA
valid_test_train_groupby1=valid_test_train_groupby.na.fill(value=avg_lookup.select("avg_DAY_OF_WEEKa").first()[0],subset=['avg_DAY_OF_WEEK'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_CRS_DEP_TIMEa").first()[0],subset=['avg_CRS_DEP_TIME'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_CRS_ELAPSED_TIMEa").first()[0],subset=['avg_CRS_ELAPSED_TIME'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DISTANCEa").first()[0],subset=['avg_DISTANCE'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("min_FIRST_DEPa").first()[0],subset=['min_FIRST_DEP'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("min_PREVIOUS_DELAYa").first()[0],subset=['min_PREVIOUS_DELAY'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_LATITUDEa").first()[0],subset=['avg_LATITUDE'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_LONGITUDEa").first()[0],subset=['avg_LONGITUDE'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_ELEVATIONa").first()[0],subset=['avg_ELEVATION'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_WND_SPEEDa").first()[0],subset=['avg_WND_SPEED'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_CIG_HEIGHTa").first()[0],subset=['avg_CIG_HEIGHT'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_VIS_DISTa").first()[0],subset=['avg_VIS_DIST'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_TEMPa").first()[0],subset=['avg_TEMP'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEW_TEMPa").first()[0],subset=['avg_DEW_TEMP'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_SLPRESSa").first()[0],subset=['avg_SLPRESS'])

valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_LATITUDEa").first()[0],subset=['avg_DEST_LATITUDE'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_LONGITUDEa").first()[0],subset=['avg_DEST_LONGITUDE'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_ELEVATIONa").first()[0],subset=['avg_DEST_ELEVATION'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_WND_SPEEDa").first()[0],subset=['avg_DEST_WND_SPEED'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_CIG_HEIGHTa").first()[0],subset=['avg_DEST_CIG_HEIGHT'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_VIS_DISTa").first()[0],subset=['avg_DEST_VIS_DIST'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_TEMPa").first()[0],subset=['avg_DEST_TEMP'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_DEW_TEMPa").first()[0],subset=['avg_DEST_DEW_TEMP'])
valid_test_train_groupby1=valid_test_train_groupby1.na.fill(value=avg_lookup.select("avg_DEST_SLPRESSa").first()[0],subset=['avg_DEST_SLPRESS'])
#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby1", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_train_groupby1.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby1") 

avg_DAY_OF_WEEKa avg_CRS_DEP_TIMEa avg_CRS_ELAPSED_TIMEa avg_DISTANCEa min_FIRST_DEPa min_PREVIOUS_DELAYa avg_LATITUDEa avg_LONGITUDEa avg_ELEVATIONa avg_WND_SPEEDa avg_CIG_HEIGHTa avg_VIS_DISTa avg_TEMPa avg_DEW_TEMPa avg_SLPRESSa avg_DEST_LATITUDEa avg_DEST_LONGITUDEa avg_DEST_ELEVATIONa avg_DEST_WND_SPEEDa avg_DEST_CIG_HEIGHTa avg_DEST_VIS_DISTa avg_DEST_TEMPa avg_DEST_DEW_TEMPa avg_DEST_SLPRESSa 3.942869869943395 1336.1695987819908 145.05387984885908 846.0186153945617 0 0 36.66500090109792 -96.0239866126912 253.3793025421035 38.581142655405 13082.74633962568 15341.070194213306 173.06952671824973 84.81701658819989 10165.1129698825 36.66381468722042 -96.05805652637845 253.06262291705212 38.49919856590109 13135.569034051387 15351.528574847283 173.61805946460262 85.14554648449783 10165.283138336996

#### Finally, impute the suspect or erroneous, nulls, and 99999 (missing) data in the full table with these averages

In [0]:
#Read Data

# 3 MONTH DATA
valid_test_3m_train_3m_groupby1 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_train_3m_groupby1/part-00*.parquet")

# FULL DATA
valid_test_train_groupby1 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_train_groupby1/part-00*.parquet")

In [0]:
#Second, impute suspect or erroneous, nulls, and 99999's readings.

#For airports missing from PageRank helper function, impute nulls as 1/N (N is number of airports in pagerank calculated from training)
unique_pr_airports = airportPR_ordered_df.count()   #This is total of unique airports in pagerank calculated from training data
#1/N = 0.0030211480362537764

# 3 MONTH DATA
# valid_test_3m_pr.describe().display()
#columns: [YEAR, MONTH, DAY_OF_WEEK, OP_UNIQUE_CARRIER, ORIGIN, ORIGIN_STATE_ABR, DEST, DEST_STATE_ABR, CRS_DEP_TIME, CRS_ELAPSED_TIME, DISTANCE, FIRST_DEP, PREVIOUS_DELAY, FLIGHTS_PER_DAY, DELAY, LATITUDE, LONGITUDE, ELEVATION, REPORT_TYPE, WND_SPEED, WND_SPEED_QUAL, CIG_HEIGHT, CIG_QUAL, VIS_DIST, VIS_DIST_QUAL, VIS_VAR, VIS_VAR_QUAL, TEMP, TEMP_QUAL, DEW_TEMP, DEW_TEMP_QUAL, SLPRESS, SLPRESS_QUAL, avg_DAY_OF_WEEK, avg_CRS_DEP_TIME, avg_CRS_ELAPSED_TIME, avg_DISTANCE, min_FIRST_DEP, min_PREVIOUS_DELAY, avg_LATITUDE, avg_LONGITUDE, avg_ELEVATION, avg_WND_SPEED, avg_CIG_HEIGHT, avg_VIS_DIST, avg_TEMP, avg_DEW_TEMP, avg_SLPRESS]

valid_test_3m_train_3m_groupby1.registerTempTable("valid_test_3m_train_3m_groupby1_tt")

valid_test_3m_imputed=spark.sql("""SELECT YEAR, MONTH, DAY_OF_WEEK, OP_UNIQUE_CARRIER, ORIGIN, ORIGIN_STATE_ABR, DEST, DEST_STATE_ABR, FLIGHTS_PER_DAY, DELAY, REPORT_TYPE, WND_SPEED_QUAL, CIG_QUAL, VIS_DIST_QUAL, VIS_VAR, VIS_VAR_QUAL, TEMP_QUAL, DEW_TEMP_QUAL, SLPRESS_QUAL, DEST_REPORT_TYPE, DEST_WND_SPEED_QUAL, DEST_CIG_QUAL, DEST_VIS_DIST_QUAL, DEST_VIS_VAR, DEST_VIS_VAR_QUAL, DEST_TEMP_QUAL, DEST_DEW_TEMP_QUAL, DEST_SLPRESS_QUAL, avg_DAY_OF_WEEK, avg_CRS_DEP_TIME, avg_CRS_ELAPSED_TIME, avg_DISTANCE, min_FIRST_DEP, min_PREVIOUS_DELAY, avg_LATITUDE, avg_LONGITUDE, avg_ELEVATION, avg_WND_SPEED, avg_CIG_HEIGHT, avg_VIS_DIST, avg_TEMP, avg_DEW_TEMP, avg_SLPRESS, avg_DEST_LATITUDE, avg_DEST_LONGITUDE, avg_DEST_ELEVATION, avg_DEST_WND_SPEED, avg_DEST_CIG_HEIGHT, avg_DEST_VIS_DIST, avg_DEST_TEMP, avg_DEST_DEW_TEMP, avg_DEST_SLPRESS, 
              
              case when CRS_DEP_TIME IS NULL then avg_CRS_DEP_TIME else CRS_DEP_TIME end as CRS_DEP_TIME,
              case when CRS_ELAPSED_TIME IS NULL then avg_CRS_ELAPSED_TIME else CRS_ELAPSED_TIME end as CRS_ELAPSED_TIME,
              case when DISTANCE IS NULL then avg_DISTANCE else DISTANCE end as DISTANCE,
              case when FIRST_DEP IS NULL then min_FIRST_DEP else FIRST_DEP end as FIRST_DEP,
              case when PREVIOUS_DELAY IS NULL then min_PREVIOUS_DELAY else PREVIOUS_DELAY end as PREVIOUS_DELAY,
              case when LATITUDE IS NULL then avg_LATITUDE else LATITUDE end as LATITUDE,
              case when LONGITUDE IS NULL then avg_LONGITUDE else LONGITUDE end as LONGITUDE,
              case when ELEVATION IS NULL then avg_ELEVATION else ELEVATION end as ELEVATION,
              
              case when WND_SPEED IS NULL or WND_SPEED=9999 or WND_SPEED_QUAL=2 or WND_SPEED_QUAL=3 or WND_SPEED_QUAL=6 or WND_SPEED_QUAL=7 
              then avg_WND_SPEED else WND_SPEED end as WND_SPEED,
              
              case when CIG_HEIGHT IS NULL or CIG_HEIGHT=99999 or CIG_QUAL=2 or CIG_QUAL=3 or CIG_QUAL=6 or CIG_QUAL=7
              then avg_CIG_HEIGHT else CIG_HEIGHT end as CIG_HEIGHT,
              
              case when VIS_DIST IS NULL or VIS_DIST=999999 or VIS_DIST_QUAL=2 or VIS_DIST_QUAL=3 or VIS_DIST_QUAL=6 or VIS_DIST_QUAL=7
              then avg_VIS_DIST else VIS_DIST end as VIS_DIST,
              
              case when TEMP IS NULL or trim(TEMP)=9999 or TEMP_QUAL=2 or TEMP_QUAL=3 or TEMP_QUAL=6 or TEMP_QUAL=7
              then avg_TEMP else TEMP end as TEMP,
              
              case when DEW_TEMP IS NULL or DEW_TEMP=9999 or DEW_TEMP_QUAL=2 or DEW_TEMP_QUAL=3 or DEW_TEMP_QUAL=6 or DEW_TEMP_QUAL=7
              then avg_DEW_TEMP else DEW_TEMP end as DEW_TEMP,
              
              case when SLPRESS IS NULL or SLPRESS=99999 or SLPRESS_QUAL=2 or SLPRESS_QUAL=3 or SLPRESS_QUAL=6 or SLPRESS_QUAL=7
              then avg_SLPRESS else SLPRESS end as SLPRESS,
              
              case when PAGERANK IS NULL then 0.0030211480362537764 else PAGERANK end as PAGERANK,


              case when DEST_LATITUDE IS NULL then avg_DEST_LATITUDE else DEST_LATITUDE end as DEST_LATITUDE,
              case when DEST_LONGITUDE IS NULL then avg_DEST_LONGITUDE else DEST_LONGITUDE end as DEST_LONGITUDE,
              case when DEST_ELEVATION IS NULL then avg_DEST_ELEVATION else DEST_ELEVATION end as DEST_ELEVATION,
              
              case when DEST_WND_SPEED IS NULL or DEST_WND_SPEED=9999 or DEST_WND_SPEED_QUAL=2 or DEST_WND_SPEED_QUAL=3 or DEST_WND_SPEED_QUAL=6 or DEST_WND_SPEED_QUAL=7 
              then avg_DEST_WND_SPEED else DEST_WND_SPEED end as DEST_WND_SPEED,
              
              case when DEST_CIG_HEIGHT IS NULL or DEST_CIG_HEIGHT=99999 or DEST_CIG_QUAL=2 or DEST_CIG_QUAL=3 or DEST_CIG_QUAL=6 or DEST_CIG_QUAL=7
              then avg_DEST_CIG_HEIGHT else DEST_CIG_HEIGHT end as DEST_CIG_HEIGHT,
              
              case when DEST_VIS_DIST IS NULL or DEST_VIS_DIST=999999 or DEST_VIS_DIST_QUAL=2 or DEST_VIS_DIST_QUAL=3 or DEST_VIS_DIST_QUAL=6 or DEST_VIS_DIST_QUAL=7
              then avg_DEST_VIS_DIST else DEST_VIS_DIST end as DEST_VIS_DIST,
              
              case when DEST_TEMP IS NULL or DEST_TEMP=9999 or DEST_TEMP_QUAL=2 or DEST_TEMP_QUAL=3 or DEST_TEMP_QUAL=6 or DEST_TEMP_QUAL=7
              then avg_DEST_TEMP else DEST_TEMP end as DEST_TEMP,
              
              case when DEST_DEW_TEMP IS NULL or DEST_DEW_TEMP=9999 or DEST_DEW_TEMP_QUAL=2 or DEST_DEW_TEMP_QUAL=3 or DEST_DEW_TEMP_QUAL=6 or DEST_DEW_TEMP_QUAL=7
              then avg_DEST_DEW_TEMP else DEST_DEW_TEMP end as DEST_DEW_TEMP,
              
              case when DEST_SLPRESS IS NULL or DEST_SLPRESS=99999 or DEST_SLPRESS_QUAL=2 or DEST_SLPRESS_QUAL=3 or DEST_SLPRESS_QUAL=6 or DEST_SLPRESS_QUAL=7
              then avg_DEST_SLPRESS else DEST_SLPRESS end as DEST_SLPRESS   
             
             FROM valid_test_3m_train_3m_groupby1_tt
              """)

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_imputed", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_3m_imputed.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_imputed")  

#######################################

# FULL DATA

#columns: [YEAR, MONTH, DAY_OF_WEEK, OP_UNIQUE_CARRIER, ORIGIN, ORIGIN_STATE_ABR, DEST, DEST_STATE_ABR, CRS_DEP_TIME, CRS_ELAPSED_TIME, DISTANCE, FIRST_DEP, PREVIOUS_DELAY, DELAY, LATITUDE, LONGITUDE, ELEVATION, REPORT_TYPE, WND_SPEED, WND_SPEED_QUAL, CIG_HEIGHT, CIG_QUAL, VIS_DIST, VIS_DIST_QUAL, VIS_VAR, VIS_VAR_QUAL, TEMP, TEMP_QUAL, DEW_TEMP, DEW_TEMP_QUAL, SLPRESS, SLPRESS_QUAL, avg_DAY_OF_WEEK, avg_CRS_DEP_TIME, avg_CRS_ELAPSED_TIME, avg_DISTANCE, min_FIRST_DEP, min_PREVIOUS_DELAY, avg_LATITUDE, avg_LONGITUDE, avg_ELEVATION, avg_WND_SPEED, avg_CIG_HEIGHT, avg_VIS_DIST, avg_TEMP, avg_DEW_TEMP, avg_SLPRESS]

valid_test_train_groupby1.registerTempTable("valid_test_train_groupby1_tt")

valid_test_imputed=spark.sql("""SELECT YEAR, MONTH, DAY_OF_WEEK, OP_UNIQUE_CARRIER, ORIGIN, ORIGIN_STATE_ABR, DEST, DEST_STATE_ABR, FLIGHTS_PER_DAY, DELAY, REPORT_TYPE, WND_SPEED_QUAL, CIG_QUAL, VIS_DIST_QUAL, VIS_VAR, VIS_VAR_QUAL, TEMP_QUAL, DEW_TEMP_QUAL, SLPRESS_QUAL, DEST_REPORT_TYPE, DEST_WND_SPEED_QUAL, DEST_CIG_QUAL, DEST_VIS_DIST_QUAL, DEST_VIS_VAR, DEST_VIS_VAR_QUAL, DEST_TEMP_QUAL, DEST_DEW_TEMP_QUAL, DEST_SLPRESS_QUAL, avg_DAY_OF_WEEK, avg_CRS_DEP_TIME, avg_CRS_ELAPSED_TIME, avg_DISTANCE, min_FIRST_DEP, min_PREVIOUS_DELAY, avg_LATITUDE, avg_LONGITUDE, avg_ELEVATION, avg_WND_SPEED, avg_CIG_HEIGHT, avg_VIS_DIST, avg_TEMP, avg_DEW_TEMP, avg_SLPRESS, avg_DEST_LATITUDE, avg_DEST_LONGITUDE, avg_DEST_ELEVATION, avg_DEST_WND_SPEED, avg_DEST_CIG_HEIGHT, avg_DEST_VIS_DIST, avg_DEST_TEMP, avg_DEST_DEW_TEMP, avg_DEST_SLPRESS,  
              
              case when CRS_DEP_TIME IS NULL then avg_CRS_DEP_TIME else CRS_DEP_TIME end as CRS_DEP_TIME,
              case when CRS_ELAPSED_TIME IS NULL then avg_CRS_ELAPSED_TIME else CRS_ELAPSED_TIME end as CRS_ELAPSED_TIME,
              case when DISTANCE IS NULL then avg_DISTANCE else DISTANCE end as DISTANCE,
              case when FIRST_DEP IS NULL then min_FIRST_DEP else FIRST_DEP end as FIRST_DEP,
              case when PREVIOUS_DELAY IS NULL then min_PREVIOUS_DELAY else PREVIOUS_DELAY end as PREVIOUS_DELAY,
              case when LATITUDE IS NULL then avg_LATITUDE else LATITUDE end as LATITUDE,
              case when LONGITUDE IS NULL then avg_LONGITUDE else LONGITUDE end as LONGITUDE,
              case when ELEVATION IS NULL then avg_ELEVATION else ELEVATION end as ELEVATION,
              
              case when WND_SPEED IS NULL or WND_SPEED=9999 or WND_SPEED_QUAL=2 or WND_SPEED_QUAL=3 or WND_SPEED_QUAL=6 or WND_SPEED_QUAL=7 
              then avg_WND_SPEED else WND_SPEED end as WND_SPEED,
              
              case when CIG_HEIGHT IS NULL or CIG_HEIGHT=99999 or CIG_QUAL=2 or CIG_QUAL=3 or CIG_QUAL=6 or CIG_QUAL=7
              then avg_CIG_HEIGHT else CIG_HEIGHT end as CIG_HEIGHT,
              
              case when VIS_DIST IS NULL or VIS_DIST=999999 or VIS_DIST_QUAL=2 or VIS_DIST_QUAL=3 or VIS_DIST_QUAL=6 or VIS_DIST_QUAL=7
              then avg_VIS_DIST else VIS_DIST end as VIS_DIST,
              
              case when (trim(TEMP) IS NULL or trim(TEMP)=9999 or TEMP_QUAL=2 or TEMP_QUAL=3 or TEMP_QUAL=6 or TEMP_QUAL=7)
              then avg_TEMP else TEMP end as TEMP,
              
              case when DEW_TEMP IS NULL or DEW_TEMP=9999 or DEW_TEMP_QUAL=2 or DEW_TEMP_QUAL=3 or DEW_TEMP_QUAL=6 or DEW_TEMP_QUAL=7
              then avg_DEW_TEMP else DEW_TEMP end as DEW_TEMP,
              
              case when SLPRESS IS NULL or SLPRESS=99999 or SLPRESS_QUAL=2 or SLPRESS_QUAL=3 or SLPRESS_QUAL=6 or SLPRESS_QUAL=7
              then avg_SLPRESS else SLPRESS end as SLPRESS,
              
              case when PAGERANK IS NULL then 0.0030211480362537764 else PAGERANK end as PAGERANK,


              case when DEST_LATITUDE IS NULL then avg_DEST_LATITUDE else DEST_LATITUDE end as DEST_LATITUDE,
              case when DEST_LONGITUDE IS NULL then avg_DEST_LONGITUDE else DEST_LONGITUDE end as DEST_LONGITUDE,
              case when DEST_ELEVATION IS NULL then avg_DEST_ELEVATION else DEST_ELEVATION end as DEST_ELEVATION,
              
              case when DEST_WND_SPEED IS NULL or DEST_WND_SPEED=9999 or DEST_WND_SPEED_QUAL=2 or DEST_WND_SPEED_QUAL=3 or DEST_WND_SPEED_QUAL=6 or DEST_WND_SPEED_QUAL=7 
              then avg_DEST_WND_SPEED else DEST_WND_SPEED end as DEST_WND_SPEED,
              
              case when DEST_CIG_HEIGHT IS NULL or DEST_CIG_HEIGHT=99999 or DEST_CIG_QUAL=2 or DEST_CIG_QUAL=3 or DEST_CIG_QUAL=6 or DEST_CIG_QUAL=7
              then avg_DEST_CIG_HEIGHT else DEST_CIG_HEIGHT end as DEST_CIG_HEIGHT,
              
              case when DEST_VIS_DIST IS NULL or DEST_VIS_DIST=999999 or DEST_VIS_DIST_QUAL=2 or DEST_VIS_DIST_QUAL=3 or DEST_VIS_DIST_QUAL=6 or DEST_VIS_DIST_QUAL=7
              then avg_DEST_VIS_DIST else DEST_VIS_DIST end as DEST_VIS_DIST,
              
              case when DEST_TEMP IS NULL or DEST_TEMP=9999 or DEST_TEMP_QUAL=2 or DEST_TEMP_QUAL=3 or DEST_TEMP_QUAL=6 or DEST_TEMP_QUAL=7
              then avg_DEST_TEMP else DEST_TEMP end as DEST_TEMP,
              
              case when DEST_DEW_TEMP IS NULL or DEST_DEW_TEMP=9999 or DEST_DEW_TEMP_QUAL=2 or DEST_DEW_TEMP_QUAL=3 or DEST_DEW_TEMP_QUAL=6 or DEST_DEW_TEMP_QUAL=7
              then avg_DEST_DEW_TEMP else DEST_DEW_TEMP end as DEST_DEW_TEMP,
              
              case when DEST_SLPRESS IS NULL or DEST_SLPRESS=9 or DEST_SLPRESS_QUAL=2 or DEST_SLPRESS_QUAL=3 or DEST_SLPRESS_QUAL=6 or DEST_SLPRESS_QUAL=7
              then avg_DEST_SLPRESS else DEST_SLPRESS end as DEST_SLPRESS   


             FROM valid_test_train_groupby1_tt
              """)


#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_imputed", True)      #remove file if there already is an existing one, be careful with this!!!
valid_test_imputed.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_imputed")  

In [0]:
#Read Data

# 3 MONTH DATA
valid_test_3m_imputed = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m_imputed/part-00*.parquet")
valid_test_3m_imputed.display()

# FULL DATA
valid_test_imputed = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_imputed/part-00*.parquet")
# valid_test_imputed.display()

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR FLIGHTS_PER_DAY DELAY REPORT_TYPE WND_SPEED_QUAL CIG_QUAL VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP_QUAL DEW_TEMP_QUAL SLPRESS_QUAL DEST_REPORT_TYPE DEST_WND_SPEED_QUAL DEST_CIG_QUAL DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP_QUAL DEST_DEW_TEMP_QUAL DEST_SLPRESS_QUAL avg_DAY_OF_WEEK avg_CRS_DEP_TIME avg_CRS_ELAPSED_TIME avg_DISTANCE min_FIRST_DEP min_PREVIOUS_DELAY avg_LATITUDE avg_LONGITUDE avg_ELEVATION avg_WND_SPEED avg_CIG_HEIGHT avg_VIS_DIST avg_TEMP avg_DEW_TEMP avg_SLPRESS avg_DEST_LATITUDE avg_DEST_LONGITUDE avg_DEST_ELEVATION avg_DEST_WND_SPEED avg_DEST_CIG_HEIGHT avg_DEST_VIS_DIST avg_DEST_TEMP avg_DEST_DEW_TEMP avg_DEST_SLPRESS CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY LATITUDE LONGITUDE ELEVATION WND_SPEED CIG_HEIGHT VIS_DIST TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_WND_SPEED DEST_CIG_HEIGHT DEST_VIS_DIST DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS 2015 3 7 AA DFW TX ORD IL 15189 1 FM-16 5 5 5 N 5 5 5 9 FM-15 5 5 5 N 5 5 5 5 7.0 1430.4825870646766 127.28897180762853 768.8994610281924 0 0 32.897800000000046 -97.01889999999993 170.7000000000003 58.82815091210614 13971.243366500828 14818.195895522387 106.98072139303483 24.236318407960198 10194.986733001659 35.096326797263686 -95.15598506840799 289.974295190713 41.45563847429519 12014.406094527363 14616.968905472637 86.27446102819238 7.633706467661692 10195.79995854063 950.0 133.0 802.0 0 0 32.8978 -97.0189 170.7 36.0 91.0 2414.0 0.0 -6.0 10194.986733001659 0.03817073608327177 41.995 -87.9336 201.8 0.0 152.0 3219.0 -83.0 -100.0 10290.0 2015 3 7 AA IAH TX MIA FL 15189 0 FM-15 5 5 A N A 5 5 5 FM-15 5 5 5 N 5 5 5 5 7.0 1434.5062454077884 138.92652461425422 818.929463629684 0 0 29.98000000000001 -95.35999999999993 29.0 34.958486407053634 10235.256061719325 13748.89052167524 155.54665686994858 87.81520940484937 10196.4360764144 34.712629426891986 -94.77601407053636 293.8718221895664 41.812637766348274 11866.793901542984 14622.159808963997 98.89088905216752 18.53857457751653 10193.839456282145 951.0 139.0 964.0 0 0 29.98 -95.36 29.0 31.0 91.0 402.0 117.0 117.0 10226.0 0.02232401241556353 25.7881 -80.3169 8.8 41.0 22000.0 16093.0 239.0 206.0 10260.0 2015 3 7 AA JFK NY MCO FL 15189 1 FM-15 5 5 5 N 5 5 5 5 FM-15 5 5 5 N 5 5 5 5 7.0 1340.8753959873284 246.4841605068638 1455.621964097149 0 0 40.63860000000001 -73.76220000000005 3.4000000000000017 53.344244984160504 6005.921858500528 13989.043294614572 12.94350580781415 -55.46832101372756 10169.729672650476 33.386253004223875 -94.3661244561774 128.53104540654698 34.051214361140445 13106.374340021119 14823.50580781415 124.61932418162618 56.21066525871172 10194.171594508976 1459.0 183.0 944.0 0 0 40.6386 -73.7622 3.4 51.0 366.0 1207.0 -33.0 -67.0 10351.0 0.014589032926165355 28.4339 -81.325 27.4 41.0 1463.0 16093.0 256.0 206.0 10268.0 2015 3 7 AA LAX CA DFW TX 15189 1 FM-15 5 5 5 N 5 5 5 5 FM-16 5 5 5 N 5 5 5 9 7.0 1376.8017484489565 171.33248730964468 1163.6872532430907 0 0 33.938000000000045 -118.38879999999993 29.599999999999955 23.71714608009024 14597.55527354766 15065.798364354201 158.76931754089114 88.84715172024816 10184.896503102087 36.15198998025946 -106.06744339537511 300.2130851663847 36.3970671178793 11706.18358714044 14387.303440496335 100.29695431472081 21.683587140439933 10191.536661026508 1144.0 181.0 1235.0 0 1 33.938 -118.3888 29.6 21.0 22000.0 16093.0 128.0 83.0 10140.0 0.03087132783443129 32.8978 -97.0189 170.7 46.0 183.0 8047.0 17.0 11.0 10191.536661026508 2015 3 7 AA LAX CA SFO CA 15189 0 FM-15 5 5 5 N 5 5 5 5 FM-15 5 5 5 N 5 5 5 5 7.0 1376.8017484489565 171.33248730964468 1163.6872532430907 0 0 33.938000000000045 -118.38879999999993 29.599999999999955 23.71714608009024 14597.55527354766 15065.798364354201 158.76931754089114 88.84715172024816 10184.896503102087 36.15198998025946 -106.06744339537511 300.2130851663847 36.3970671178793 11706.18358714044 14387.303

In [0]:
valid_test_3m_imputed.where("DEST_TEMP = '9999'").display()

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR FLIGHTS_PER_DAY DELAY REPORT_TYPE WND_SPEED_QUAL CIG_QUAL VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP_QUAL DEW_TEMP_QUAL SLPRESS_QUAL DEST_REPORT_TYPE DEST_WND_SPEED_QUAL DEST_CIG_QUAL DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP_QUAL DEST_DEW_TEMP_QUAL DEST_SLPRESS_QUAL avg_DAY_OF_WEEK avg_CRS_DEP_TIME avg_CRS_ELAPSED_TIME avg_DISTANCE min_FIRST_DEP min_PREVIOUS_DELAY avg_LATITUDE avg_LONGITUDE avg_ELEVATION avg_WND_SPEED avg_CIG_HEIGHT avg_VIS_DIST avg_TEMP avg_DEW_TEMP avg_SLPRESS avg_DEST_LATITUDE avg_DEST_LONGITUDE avg_DEST_ELEVATION avg_DEST_WND_SPEED avg_DEST_CIG_HEIGHT avg_DEST_VIS_DIST avg_DEST_TEMP avg_DEST_DEW_TEMP avg_DEST_SLPRESS CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY LATITUDE LONGITUDE ELEVATION WND_SPEED CIG_HEIGHT VIS_DIST TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_WND_SPEED DEST_CIG_HEIGHT DEST_VIS_DIST DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS

In [0]:
#Finally, keep only columns used for next step(s).

# 3 MONTH DATA
valid_test_3m_imputed=valid_test_3m_imputed.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'FLIGHTS_PER_DAY', 'DELAY', 'REPORT_TYPE', 'CRS_DEP_TIME', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED', 'CIG_HEIGHT', 'VIS_DIST', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_WND_SPEED', 'DEST_CIG_HEIGHT', 'DEST_VIS_DIST', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS')
# print(valid_test_3m_imputed.columns)

# FULL DATA
valid_test_imputed=valid_test_imputed.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'FLIGHTS_PER_DAY', 'DELAY', 'REPORT_TYPE', 'CRS_DEP_TIME', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED', 'CIG_HEIGHT', 'VIS_DIST', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_WND_SPEED', 'DEST_CIG_HEIGHT', 'DEST_VIS_DIST', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS')
# print(valid_test_imputed.columns)

# C) Binning

Add code for creating bins for these features:

AIRLINE DATA:

Departure time (* Should be based on local time - this binning needs to occur before UTC)
* 0 - 1:59
* 2 - 3:59
* 4 - 5:59
* 6 - 7:59
* 8 - 9:59
* 10 - 11:59
* 12 - 13:59 
* 14 - 15:59 
* 16 - 17:59
* 18 - 19:59
* 20 - 21:59
* 22 - 23:59


WEATHER DATA:

Sky condition (CIG_HEIGHT)
* 0 - 21999 = Limited vertical visibility
* 22000 = Unlimited veritcal visibility

Wind Speed (based on Beaufort Scale: https://en.wikipedia.org/wiki/Beaufort_scale)
* <15 = Calm to light breeze
* <33 = Gentle breeze
* <107 = Moderate to fresh breeze
* \>=138 = Strong breeze to gale/storm

Visibility Distance
* \>= 16093 (>= 10 miles) --- most values are exactly 16093, likely indicating max visibility
* < 16093 (< 10 miles) --- group all other values below together

In [0]:
#####################################
# 3 Month Data

# change data to whatever the processed and joined dataframe is called
data_3m = valid_test_3m_imputed.withColumn('CRS_DEP_TIME',valid_test_3m_imputed.CRS_DEP_TIME.cast(FloatType()) )

#Convert departure time to bins
dep_time_buck_3m = Bucketizer(splits=[ 0, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000, 2200, float('Inf') ],inputCol="CRS_DEP_TIME", outputCol="CRS_DEP_TIME_BUCK")
air_buck_3m = dep_time_buck_3m.setHandleInvalid("keep").transform(data_3m)

#Convert wind, vis, sky to bins
wind_buck_3m = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="WND_SPEED", outputCol="WND_SPEED_BUCK")
vis_buck_3m = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="VIS_DIST", outputCol="VIS_DIST_BUCK")
sky_buck_3m = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="CIG_HEIGHT", outputCol="CIG_HEIGHT_BUCK")
w_buck_3m = wind_buck_3m.setHandleInvalid("keep").transform(air_buck_3m)   
w_buck_3m = vis_buck_3m.setHandleInvalid("keep").transform(w_buck_3m)
w_buck_3m = sky_buck_3m.setHandleInvalid("keep").transform(w_buck_3m)

wind_buck_3m_dw = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="DEST_WND_SPEED", outputCol="DEST_WND_SPEED_BUCK")
vis_buck_3m_dw = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="DEST_VIS_DIST", outputCol="DEST_VIS_DIST_BUCK")
sky_buck_3m_dw = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="DEST_CIG_HEIGHT", outputCol="DEST_CIG_HEIGHT_BUCK")
w_buck_3m = wind_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)   
w_buck_3m = vis_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)
w_buck_3m = sky_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)

# drop numeric columns (keep only features needed for modeling)
valid_test_data_3m = w_buck_3m.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
# dbutils.fs.mkdirs("dbfs:/mnt/mids-w261/team_25/")               #Made Directory in DataBricks, no need to remake
file_to_store = valid_test_data_3m                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "valid_test_data_3m"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

#####################################
# Full Data

# change data to whatever the processed and joined dataframe is called
data = valid_test_imputed.withColumn('CRS_DEP_TIME',valid_test_imputed.CRS_DEP_TIME.cast(FloatType()) )

#Convert departure time to bins
dep_time_buck = Bucketizer(splits=[ 0, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000, 2200, float('Inf') ],inputCol="CRS_DEP_TIME", outputCol="CRS_DEP_TIME_BUCK")
air_buck = dep_time_buck.setHandleInvalid("keep").transform(data)

#Convert wind, vis, sky to bins
wind_buck = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="WND_SPEED", outputCol="WND_SPEED_BUCK")
vis_buck = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="VIS_DIST", outputCol="VIS_DIST_BUCK")
sky_buck = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="CIG_HEIGHT", outputCol="CIG_HEIGHT_BUCK")
w_buck = wind_buck.setHandleInvalid("keep").transform(air_buck)   
w_buck = vis_buck.setHandleInvalid("keep").transform(w_buck)
w_buck = sky_buck.setHandleInvalid("keep").transform(w_buck)

wind_buck_dw = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="DEST_WND_SPEED", outputCol="DEST_WND_SPEED_BUCK")
vis_buck_dw = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="DEST_VIS_DIST", outputCol="DEST_VIS_DIST_BUCK")
sky_buck_dw = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="DEST_CIG_HEIGHT", outputCol="DEST_CIG_HEIGHT_BUCK")
w_buck = wind_buck_dw.setHandleInvalid("keep").transform(w_buck)   
w_buck = vis_buck_dw.setHandleInvalid("keep").transform(w_buck)
w_buck = sky_buck_dw.setHandleInvalid("keep").transform(w_buck)

# drop numeric columns (keep only features needed for modeling)
valid_test_data = w_buck.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
# dbutils.fs.mkdirs("dbfs:/mnt/mids-w261/team_25/")               #Made Directory in DataBricks, no need to remake
file_to_store = valid_test_data                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "valid_test_data"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "valid_test_data_3m"                      
valid_test_data_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# valid_test_data_3m.display()
print("valid_test_data_3m Shape:", valid_test_data_3m.count(), len(valid_test_data_3m.columns))

############################################

filename = "valid_test_data"                      
valid_test_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# valid_test_data.display()
print("valid_test_data:", valid_test_data.count(), len(valid_test_data.columns))

valid_test_data_3m Shape: 503547 36
valid_test_data: 14478697 36

## Validation/Test Data Write to DataBase

In [0]:
##########################
# 3 MONTH DATA

#Split to Validation and Test Data

validation_data_3m_dw_b = valid_test_data_3m.where("MONTH = 3")

#SAVING Spark Dataframe to Shared Directory
file_to_store = validation_data_3m_dw_b                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "validation_data_3m_dw_b"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

###########################
#FULL DATA

validation_data_dw_b = valid_test_data.where("YEAR = 2018")
test_data_dw_b = valid_test_data.where("YEAR = 2019")

#SAVING Spark Dataframe to Shared Directory
file_to_store = validation_data_dw_b                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "validation_data_dw_b"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = test_data_dw_b                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "test_data_dw_b"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

# Rename Data Files for Modeling

In [0]:
#Read Data
filename = "validation_data_3m_dw_b"                      
validation_data_3m_dw_b = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# validation_data_3m_dw_b.display()
# print("validation_data_3m_dw_b Shape:", validation_data_3m_dw_b.count(), len(validation_data_3m_dw_b.columns))

############################################

filename = "validation_data_dw_b"                      
validation_data_dw_b = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# validation_data_dw_b.display()
# print("validation_data_dw_b:", validation_data_dw_b.count(), len(validation_data_dw_b.columns))

filename = "test_data_dw_b"                      
test_data_dw_b = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# test_data_dw_b.display()
# print("test_data_dw_b:", test_data_dw_b.count(), len(test_data_dw_b.columns))

In [0]:
#Split Data to 3month baseline validation, 3 month validation, full validation and full test
validation_data_3m_baseline = validation_data_3m_dw_b.where("ORIGIN = 'ATL' or ORIGIN = 'ORD'")
validation_data_3m = validation_data_3m_dw_b
validation_data = validation_data_dw_b
test_data = test_data_dw_b

#SAVING Spark Dataframe to Shared Directory
file_to_store = validation_data_3m_baseline                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "validation_data_3m_baseline"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = validation_data_3m                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "validation_data_3m"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = validation_data                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "validation_data"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = test_data                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "test_data"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Reado 3month baseline validation, 3 month validation, full validation and full test data

#Read Data
filename = "validation_data_3m_baseline"                      
validation_data_3m_baseline = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
validation_data_3m_baseline.display()
print("validation_data_3m_baseline Shape:", validation_data_3m_baseline.count(), len(validation_data_3m_baseline.columns))

############################################

filename = "validation_data_3m"                      
validation_data_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
validation_data_3m.display()
print("validation_data_3m:", validation_data_3m.count(), len(validation_data_3m.columns))

############################################

filename = "validation_data"                      
validation_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
validation_data.display()
print("validation_data:", validation_data.count(), len(validation_data.columns))

############################################

filename = "test_data"                      
test_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
test_data.display()
print("test_data:", test_data.count(), len(test_data.columns))

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2015 3 7 AA ORD IL MSP MN 7.0 86.0 334.0 0 0 15189 41.995 -87.9336 201.8 1.0 0.0 0.0 N -56.0 -89.0 10194.58439116126 0.04737763713846122 44.8831 -93.2289 265.8 N -56.0 -150.0 10268.0 2.0 1.0 1.0 1 2015 3 7 EV ATL GA CSG GA 8.0 44.0 83.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 56.0 44.0 10303.0 0.06178103047926055 32.5161 -84.9422 119.5 N 83.0 61.0 10293.0 1.0 1.0 0.0 0 2015 3 7 MQ ORD IL CMI IL 6.0 47.0 135.0 0 0 15189 41.995 -87.9336 201.8 1.0 0.0 0.0 N -67.0 -89.0 10289.0 0.04737763713846122 40.03972 -88.27778 229.8 N -44.0 -56.0 10290.0 0.0 0.0 0.0 1 2015 3 7 OO ATL GA ORD IL 4.0 132.0 606.0 0 1 15189 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 30.0 10.0 10203.477010504563 0.06178103047926055 41.995 -87.9336 201.8 N -111.0 -128.0 10301.0 1.0 0.0 0.0 0 2015 3 7 UA ORD IL SFO CA 9.0 287.0 1846.0 0 0 15189 41.995 -87.9336 201.8 2.0 0.0 1.0 N -44.0 -94.0 10260.0 0.04737763713846122 37.6197 -122.3647 2.4 N 172.0 39.0 10139.0 1.0 1.0 1.0 1 2015 3 1 DL ATL GA DFW TX 5.0 153.0 731.0 0 0 16427 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 83.0 72.0 10268.0 0.06178103047926055 32.8978 -97.0189 170.7 N 6.0 0.0 10289.0 2.0 0.0 0.0 1 2015 3 1 DL ATL GA MSP MN 4.0 161.0 907.0 0 0 16427 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 78.0 72.0 10260.0 0.06178103047926055 44.8831 -93.2289 265.8 N -111.0 -144.0 10334.0 1.0 1.0 1.0 0 2015 3 1 DL ATL GA RDU NC 11.0 85.0 356.0 0 0 16427 33.6301 -84.4418 307.8 0.0 0.0 1.0 N 122.0 100.0 10248.0 0.06178103047926055 35.8923 -78.7819 126.8 N 94.0 -50.0 10263.0 0.0 1.0 0.0 0 2015 3 1 EV ATL GA GTR MS 7.0 70.0 241.0 0 0 16427 33.6301 -84.4418 307.8 2.0 0.0 1.0 N 161.0 106.0 10262.0 0.06178103047926055 33.45 -88.58333 80.5 N 80.0 60.0 10208.477611940298 2.0 0.0 0.0 0 2015 3 1 EV ORD IL GRB WI 4.0 60.0 173.0 0 0 16427 41.995 -87.9336 201.8 2.0 1.0 1.0 N -100.0 -133.0 10329.0 0.04737763713846122 44.4794 -88.1366 209.4 N -111.0 -144.0 10319.0 2.0 0.0 1.0 0 2015 3 1 EV ORD IL MSN WI 4.0 57.0 108.0 0 0 16427 41.995 -87.9336 201.8 1.0 1.0 1.0 N -89.0 -128.0 10335.0 0.04737763713846122 43.1405 -89.3452 264.0 N -139.0 -161.0 10333.0 1.0 0.0 1.0 0 2015 3 1 MQ ORD IL CLE OH 6.0 72.0 315.0 0 0 16427 41.995 -87.9336 201.8 0.0 1.0 1.0 N -28.0 -122.0 10344.0 0.04737763713846122 41.4057 -81.852 238.0 N -33.0 -106.0 10334.0 1.0 1.0 1.0 0 2015 3 1 MQ ORD IL CMH OH 4.0 74.0 296.0 0 0 16427 41.995 -87.9336 201.8 2.0 1.0 1.0 N -100.0 -133.0 10323.0 0.04737763713846122 39.9907 -82.877 248.7 N -67.0 -106.0 10317.0 2.0 0.0 0.0 0 2015 3 1 MQ ORD IL CMI IL 10.0 47.0 135.0 0 0 16427 41.995 -87.9336 201.8 2.0 0.0 1.0 N -22.0 -72.0 10291.0 0.04737763713846122 40.03972 -88.27778 229.8 N -50.0 -83.0 10303.0 1.0 0.0 1.0 0 2015 3 1 UA ORD IL DCA VA 6.0 113.0 612.0 0 1 16427 41.995 -87.9336 201.8 0.0 1.0 1.0 N -28.0 -122.0 10344.0 0.04737763713846122 38.8472 -77.03454 3.0 N 72.0 -44.0 10256.0 2.0 1.0 1.0 0 2015 3 1 UA ORD IL PDX OR 10.0 276.0 1739.0 0 0 16427 41.995 -87.9336 201.8 2.0 0.0 1.0 N -22.0 -72.0 10291.0 0.04737763713846122 45.5958 -122.6093 5.8 N 128.0 33.0 10150.0 2.0 1.0 1.0 1 2015 3 2 AA ORD IL FLL FL 2.0 177.0 1182.0 0 0 15974 41.995 -87.9336 201.8 2.0 0.0 0.0 N -33.0 -83.0 10194.0 0.04737763713846122 26.07875 -80.16217 3.4 N 222.0 200.0 10204.0 2.0 1.0 1.0 0 2015 3 2 AA ORD IL LAX CA 9.0 275.0 1744.0 0 0 15974 41.995 -87.9336 201.8 2.0 0.0 1.0 N 11.0 -17.0 10061.0 0.04737763713846122 33.938 -118.3888 29.6 N 156.0 83.0 10126.0 2.0 1.0 1.0 0 2015 3 2 DL ATL GA FLL FL 6.0 108.0 581.0 0 0 15974 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 117.0 106.0 10241.0 0.06178103047926055 26.07875 -80.16217 3.4 N 250.0 200.0 

validation_data_3m_baseline Shape: 58822 36

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2015 3 7 AA DFW TX ORD IL 4.0 133.0 802.0 0 0 15189 32.8978 -97.0189 170.7 2.0 0.0 0.0 N 0.0 -6.0 10194.986733001659 0.03817073608327177 41.995 -87.9336 201.8 N -83.0 -100.0 10290.0 0.0 0.0 0.0 1 2015 3 7 AA IAH TX MIA FL 4.0 139.0 964.0 0 0 15189 29.98 -95.36 29.0 1.0 0.0 0.0 N 117.0 117.0 10226.0 0.02232401241556353 25.7881 -80.3169 8.8 N 239.0 206.0 10260.0 2.0 1.0 1.0 0 2015 3 7 AA JFK NY MCO FL 7.0 183.0 944.0 0 0 15189 40.6386 -73.7622 3.4 2.0 0.0 0.0 N -33.0 -67.0 10351.0 0.014589032926165355 28.4339 -81.325 27.4 N 256.0 206.0 10268.0 2.0 1.0 0.0 1 2015 3 7 AA LAX CA DFW TX 5.0 181.0 1235.0 0 1 15189 33.938 -118.3888 29.6 1.0 1.0 1.0 N 128.0 83.0 10140.0 0.03087132783443129 32.8978 -97.0189 170.7 N 17.0 11.0 10191.536661026508 2.0 0.0 0.0 1 2015 3 7 AA LAX CA SFO CA 8.0 80.0 337.0 0 0 15189 33.938 -118.3888 29.6 2.0 0.0 1.0 N 161.0 83.0 10118.0 0.03087132783443129 37.6197 -122.3647 2.4 N 172.0 39.0 10139.0 1.0 1.0 1.0 0 2015 3 7 AA LGA NY DFW TX 3.0 251.0 1389.0 0 0 15189 40.7792 -73.88 3.4 0.0 1.0 1.0 N -44.0 -122.0 10390.0 0.014125221879033551 32.8978 -97.0189 170.7 N 0.0 -6.0 10200.56747600226 2.0 0.0 0.0 1 2015 3 7 AA MIA FL SFO CA 9.0 393.0 2585.0 0 0 15189 25.7881 -80.3169 8.8 2.0 1.0 1.0 N 272.0 189.0 10242.0 0.010211556958918115 37.6197 -122.3647 2.4 N 161.0 22.0 10146.0 0.0 1.0 1.0 0 2015 3 7 AA STL MO DFW TX 4.0 115.0 550.0 0 0 15189 38.7525 -90.3736 161.8 0.0 0.0 0.0 N -28.0 -44.0 10298.0 0.0076554971275557965 32.8978 -97.0189 170.7 N 0.0 -6.0 10265.0 2.0 0.0 0.0 1 2015 3 7 AS OAK CA OGG HI 3.0 339.0 2349.0 0 0 15189 37.72139 -122.22083 1.8 2.0 1.0 1.0 N 83.0 61.0 10141.0 0.006969406014494394 20.89972 -156.42861 15.5 N 210.0 200.0 10193.124653739613 1.0 0.0 0.0 0 2015 3 7 B6 FLL FL DCA VA 10.0 149.0 899.0 0 0 15189 26.07875 -80.16217 3.4 2.0 1.0 1.0 N 239.0 206.0 10243.0 0.012174883582663549 38.8472 -77.03454 3.0 N 6.0 -17.0 10274.0 2.0 0.0 0.0 1 2015 3 7 DL ATL GA CVG KY 9.0 89.0 373.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 78.0 56.0 10296.0 0.06178103047926055 39.0444 -84.6724 269.1 N 11.0 -6.0 10257.0 1.0 0.0 0.0 0 2015 3 7 DL ATL GA DCA VA 10.0 103.0 547.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 78.0 56.0 10296.0 0.06178103047926055 38.8472 -77.03454 3.0 N 6.0 -17.0 10274.0 2.0 0.0 0.0 1 2015 3 7 DL ATL GA DCA VA 10.0 101.0 547.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 70.0 60.0 10203.477010504563 0.06178103047926055 38.8472 -77.03454 3.0 N 10.0 -20.0 10194.36214913036 1.0 1.0 0.0 0 2015 3 7 DL ATL GA DFW TX 8.0 155.0 731.0 0 1 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 56.0 44.0 10303.0 0.06178103047926055 32.8978 -97.0189 170.7 N 17.0 11.0 10276.0 2.0 0.0 0.0 1 2015 3 7 DL ATL GA JAN MS 6.0 84.0 341.0 0 1 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 33.0 17.0 10331.0 0.06178103047926055 32.3205 -90.0777 100.6 N 128.0 111.0 10272.0 2.0 0.0 0.0 0 2015 3 7 DL ATL GA LAX CA 5.0 313.0 1947.0 0 0 15189 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 22.0 11.0 10329.0 0.06178103047926055 33.938 -118.3888 29.6 N 111.0 83.0 10126.0 2.0 1.0 0.0 1 2015 3 7 DL ATL GA LGA NY 8.0 138.0 762.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 56.0 44.0 10303.0 0.06178103047926055 40.7792 -73.88 3.4 N -39.0 -61.0 10331.0 2.0 0.0 0.0 1 2015 3 7 DL ATL GA SAT TX 7.0 164.0 874.0 0 0 15189 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 44.0 33.0 10322.0 0.06178103047926055 29.5443 -98.4839 240.5 N 67.0 50.0 10237.0 2.0 0.0 0.0 0 2015 3 7 DL ATL GA STL MO 7.0 112.0 484.0 0 0 15189 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 56.0 39.0 10314.0 0.06178103047926055 38.7525 -90.3736 161.8 N -10.0 -40.0 101

validation_data_3m: 503547 36

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2018 12 1 9E AGS GA ATL GA 6.0 69.0 143.0 0 0 16709 33.3644 -81.9633 40.2 1.0 0.0 0.0 N 189.0 189.0 10214.0 8.247055865650812E-4 33.6301 -84.4418 307.8 N 167.0 156.0 99999.0 1.0 0.0 0.0 1 2018 12 1 9E AGS GA ATL GA 4.0 71.0 143.0 0 0 16709 33.3644 -81.9633 40.2 0.0 0.0 0.0 N 150.0 150.0 10208.0 8.247055865650812E-4 33.6301 -84.4418 307.8 N 133.0 128.0 10195.0 2.0 0.0 0.0 0 2018 12 1 9E BHM AL ATL GA 6.0 65.0 134.0 0 0 16709 33.56556 -86.745 187.5 2.0 0.0 1.0 N 217.0 172.0 10151.0 0.0021165652216008973 33.6301 -84.4418 307.8 N 178.0 167.0 99999.0 2.0 0.0 0.0 1 2018 12 1 9E HRL TX MSP MN 7.0 191.0 1310.0 0 0 16709 26.22806 -97.65417 10.4 1.0 0.0 1.0 N 144.0 72.0 10146.0 8.289280080042082E-4 44.8831 -93.2289 265.8 N -28.0 -50.0 10109.0 2.0 1.0 0.0 1 2018 12 1 AA BDL CT CLT NC 8.0 132.0 644.0 0 0 16709 41.9375 -72.6819 53.3 2.0 0.0 1.0 N 56.0 -6.0 10248.0 0.003175480977679705 35.2236 -80.9552 221.9 N 156.0 156.0 10173.0 1.0 0.0 0.0 0 2018 12 1 AA DCA VA RSW FL 4.0 168.0 892.0 0 0 16709 38.8472 -77.03454 3.0 1.0 0.0 1.0 N 50.0 22.0 10256.0 0.010509557105859428 26.53611 -81.755 9.4 N 172.0 167.0 10205.0 1.0 1.0 1.0 0 2018 12 1 AA DFW TX CLT NC 3.0 151.0 936.0 0 0 16709 32.8978 -97.0189 170.7 2.0 0.0 1.0 N 44.0 33.0 10074.0 0.03817073608327177 35.2236 -80.9552 221.9 N 122.0 122.0 10217.0 1.0 0.0 0.0 0 2018 12 1 AA DFW TX IND IN 6.0 124.0 761.0 0 0 16709 32.8978 -97.0189 170.7 2.0 0.0 1.0 N 67.0 50.0 10096.0 0.03817073608327177 39.72517 -86.28168 241.1 N 78.0 78.0 10075.0 2.0 0.0 0.0 0 2018 12 1 AA DFW TX SEA WA 7.0 271.0 1660.0 0 0 16709 32.8978 -97.0189 170.7 2.0 0.0 1.0 N 139.0 28.0 10075.0 0.03817073608327177 47.4444 -122.3138 112.8 N 33.0 22.0 10330.0 1.0 0.0 0.0 0 2018 12 1 AA DFW TX SFO CA 4.0 241.0 1464.0 0 0 16709 32.8978 -97.0189 170.7 1.0 0.0 1.0 N 50.0 39.0 10079.0 0.03817073608327177 37.6197 -122.3647 2.4 N 83.0 22.0 10159.0 2.0 1.0 1.0 0 2018 12 1 AA FLL FL ORD IL 8.0 216.0 1182.0 0 0 16709 26.07875 -80.16217 3.4 2.0 1.0 1.0 N 267.0 222.0 10198.0 0.012174883582663549 41.96019 -87.93162 201.8 N 33.0 33.0 10017.0 2.0 0.0 0.0 0 2018 12 1 AA LAX CA STL MO 8.0 208.0 1592.0 0 0 16709 33.938 -118.3888 29.6 2.0 0.0 1.0 N 161.0 89.0 10093.0 0.03087132783443129 38.7525 -90.3736 161.8 N 72.0 44.0 10080.0 2.0 1.0 0.0 0 2018 12 1 AA LGA NY DFW TX 5.0 263.0 1389.0 0 0 16709 40.7792 -73.88 3.4 1.0 0.0 1.0 N 33.0 17.0 10283.0 0.014125221879033551 32.8978 -97.0189 170.7 N 44.0 33.0 10079.0 1.0 1.0 0.0 0 2018 12 1 AA SAN CA JFK NY 3.0 318.0 2446.0 0 0 16709 32.7336 -117.1831 4.6 2.0 0.0 1.0 N 150.0 94.0 10130.0 0.010993872150786075 40.6386 -73.7622 3.4 N 20.0 10.0 99999.0 1.0 1.0 0.0 1 2018 12 1 AA TUS AZ DFW TX 3.0 134.0 813.0 0 0 16709 32.1313 -110.9552 776.9 1.0 1.0 1.0 N 33.0 -44.0 10118.0 0.0026847997308403464 32.8978 -97.0189 170.7 N 39.0 33.0 99999.0 1.0 1.0 0.0 0 2018 12 1 AS ANC AK BET AK 3.0 82.0 399.0 0 0 16709 61.169 -150.0278 36.6 2.0 1.0 1.0 N 56.0 -22.0 10047.269467584209 0.008173654734974205 60.785 -161.8293 31.1 N 0.0 -17.0 9662.0 1.0 1.0 1.0 0 2018 12 1 AS PSP CA SEA WA 5.0 173.0 987.0 0 0 16709 33.8222 -116.5043 124.7 0.0 0.0 1.0 N 100.0 -6.0 10134.0 0.001860338533866305 47.4444 -122.3138 112.8 N 11.0 0.0 10324.0 1.0 0.0 0.0 0 2018 12 1 AS SEA WA AUS TX 6.0 240.0 1770.0 0 0 16709 47.4444 -122.3138 112.8 1.0 0.0 0.0 N 22.0 11.0 10183.450709082288 0.022200771421814543 30.1831 -97.6799 146.3 N 122.0 78.0 10128.0 1.0 1.0 0.0 0 2018 12 1 AS SEA WA BOS MA 10.0 309.0 2496.0 0 0 16709 47.4444 -122.3138 112.8 1.0 1.0 1.0 N 33.0 0.0 10327.0 0.022200771421814543 42.3606 -71.0097 3.7 N 28.0 11.0 9

validation_data: 7170842 36

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2019 8 4 9E AGS GA ATL GA 2.0 60.0 143.0 0 0 22301 33.3644 -81.9633 40.2 1.0 1.0 1.0 N 250.0 222.0 10112.0 8.247055865650812E-4 33.6301 -84.4418 307.8 N 256.0 189.0 10120.0 2.0 1.0 0.0 0 2019 8 4 9E ATL GA OAJ NC 10.0 86.0 399.0 0 0 22301 33.6301 -84.4418 307.8 2.0 0.0 1.0 N 322.0 200.0 10124.0 0.06178103047926055 34.83333 -77.61667 29.3 N 328.0 222.0 10102.0 2.0 1.0 1.0 1 2019 8 4 9E BTR LA ATL GA 3.0 98.0 448.0 0 1 22301 30.5372 -91.1469 19.5 1.0 1.0 1.0 N 261.0 250.0 10139.0 0.0014464071133628263 33.6301 -84.4418 307.8 N 239.0 194.0 10122.0 1.0 1.0 0.0 0 2019 8 4 9E DTW MI BTV VT 8.0 109.0 537.0 0 0 22301 42.2313 -83.3308 192.3 2.0 1.0 1.0 N 283.0 150.0 10078.0 0.02061755116491139 44.4683 -73.1499 100.6 N 278.0 183.0 10016.0 2.0 1.0 1.0 0 2019 8 4 9E JFK NY IAD VA 8.0 115.0 228.0 0 1 22301 40.63915 -73.76401 3.4 2.0 1.0 1.0 N 272.0 233.0 10061.0 0.014589032926165355 38.93486 -77.44728 88.4 N 328.0 139.0 10078.0 2.0 1.0 1.0 1 2019 8 4 9E JFK NY PWM ME 11.0 99.0 273.0 0 0 22301 40.63915 -73.76401 3.4 3.0 0.0 0.0 N 267.0 161.0 10167.814771657779 0.014589032926165355 43.64222 -70.30444 13.7 N 217.0 183.0 10023.0 1.0 1.0 1.0 1 2019 8 4 9E JFK NY ROC NY 11.0 103.0 264.0 0 0 22301 40.63915 -73.76401 3.4 3.0 0.0 0.0 N 267.0 161.0 10167.814771657779 0.014589032926165355 43.1167 -77.6767 164.3 N 222.0 194.0 10052.0 2.0 1.0 1.0 1 2019 8 4 9E MSP MN STL MO 3.0 87.0 448.0 0 0 22301 44.8831 -93.2289 265.8 1.0 1.0 1.0 N 167.0 117.0 10120.0 0.0228724306628863 38.7525 -90.3736 161.8 N 228.0 200.0 10109.0 1.0 1.0 1.0 0 2019 8 4 9E ORF VA LGA NY 3.0 86.0 296.0 0 1 22301 36.9033 -76.1922 9.1 1.0 1.0 1.0 N 228.0 217.0 10174.867733782645 0.0018830828949039614 40.77944 -73.88035 3.4 N 217.0 183.0 10070.0 1.0 1.0 1.0 0 2019 8 4 9E RDU NC LGA NY 7.0 115.0 431.0 1 0 22301 35.8923 -78.7819 126.8 2.0 1.0 1.0 N 311.0 194.0 10109.0 0.005151502521536252 40.77944 -73.88035 3.4 N 294.0 178.0 10060.0 2.0 1.0 1.0 1 2019 8 4 AA CLT NC PHL PA 5.0 98.0 449.0 0 0 22301 35.2236 -80.9552 221.9 1.0 1.0 1.0 N 256.0 206.0 10119.0 0.015388660893576225 39.87327 -75.22678 3.0 N 228.0 200.0 99999.0 1.0 0.0 0.0 0 2019 8 4 AA CLT NC SMF CA 9.0 319.0 2244.0 0 0 22301 35.2236 -80.9552 221.9 1.0 0.0 1.0 N 328.0 178.0 10112.0 0.015388660893576225 38.69556 -121.58972 7.0 N 267.0 133.0 10127.0 2.0 1.0 1.0 1 2019 8 4 AA CMH OH LAX CA 8.0 285.0 1995.0 0 0 22301 39.9907 -82.877 248.7 2.0 0.0 1.0 N 300.0 172.0 10092.0 0.0036139633042141924 33.938 -118.3888 29.6 N 189.0 167.0 10147.0 2.0 0.0 0.0 0 2019 8 4 AA DCA VA DFW TX 2.0 194.0 1192.0 0 0 22301 38.8472 -77.03454 3.0 1.0 0.0 1.0 N 222.0 200.0 10088.0 0.010509557105859428 32.8978 -97.0189 170.7 N 300.0 200.0 10096.0 2.0 1.0 0.0 0 2019 8 4 AA DCA VA LGA NY 4.0 79.0 214.0 0 0 22301 38.8472 -77.03454 3.0 1.0 1.0 1.0 N 222.0 194.0 10089.0 0.010509557105859428 40.77944 -73.88035 3.4 N 217.0 183.0 10070.0 2.0 1.0 1.0 0 2019 8 4 AA DFW TX MSY LA 7.0 86.0 447.0 0 0 22301 32.8978 -97.0189 170.7 1.0 0.0 1.0 N 333.0 228.0 10121.0 0.03817073608327177 29.99691 -90.27751 1.2 N 306.0 228.0 10165.0 2.0 1.0 1.0 0 2019 8 4 AA DFW TX PIT PA 5.0 168.0 1067.0 0 0 22301 32.8978 -97.0189 170.7 2.0 0.0 1.0 N 283.0 228.0 10118.0 0.03817073608327177 40.4846 -80.2144 366.7 N 239.0 178.0 10093.0 2.0 1.0 1.0 0 2019 8 4 AA DFW TX SEA WA 7.0 250.0 1660.0 0 0 22301 32.8978 -97.0189 170.7 1.0 0.0 1.0 N 333.0 228.0 10121.0 0.03817073608327177 47.4444 -122.3138 112.8 N 178.0 122.0 10167.0 1.0 1.0 0.0 1 2019 8 4 AA HNL HI DFW TX 9.0 452.0 3784.0 0 0 22301 21.324 -157.9294 2.1 2.0 0.0 1.0 N 289.0 200.0 10139.0 0.009074163773956763 3

test_data: 7307855 36